In [1]:
from IPython.display import Image
from pathlib import Path
import pandas as pd
import lightgbm as lgb
from sklearn.metrics import log_loss
import math
import xgboost as xgb

In [2]:
good_classes = [9,101, 103, 104, 138, 149,269, 271, 272,274,275, 276, 277, 280 ,288,291,
                293,290,330, 331, 334, 340,341,342, 343,344, 345,346,347,348,349, 
                351, 352,353, 354,361, 362,363, 372, 386, 703,984 ,975, 979]

In [3]:
train_labels = pd.read_csv("KD/train_labels_KD.csv", index_col="seq_id")
train_labels_columns=train_labels.columns
train_labels['season'] = train_labels.index.map(lambda x: x.split("#")[0])
# scale_pos_weight=(train_labels[train_labels_columns].mean(axis=0)/train_labels.loc[train_labels.season.isin(['SER_S9', 'SER_S10']), train_labels_columns].mean(axis=0)).to_dict()
scale_pos_weight=(train_labels[train_labels_columns].mean(axis=0)/train_labels.loc[train_labels.season.isin(['SER_S9']), train_labels_columns].mean(axis=0)).to_dict()

del train_labels['season']

In [4]:
scale_pos_weight

{'aardvark': 1.056250753374268,
 'aardwolf': 0.7064722370617947,
 'baboon': 0.9928901215955798,
 'bat': inf,
 'batearedfox': 0.8033268173511552,
 'buffalo': 1.6614962450003685,
 'bushbuck': 1.7304117251898035,
 'caracal': 1.4346712988744978,
 'cattle': 0.2533466373932224,
 'cheetah': 1.3479620956870417,
 'civet': 0.8521659621408388,
 'dikdik': 1.1911672590981044,
 'duiker': 0.4026543735371904,
 'eland': 2.2229380503562055,
 'elephant': 1.2661380449416777,
 'empty': 0.9671013291147392,
 'gazellegrants': 1.5929608986294646,
 'gazellethomsons': 0.9536667996507001,
 'genet': 1.4542755029584973,
 'giraffe': 1.4436026429037736,
 'guineafowl': 2.305370178151074,
 'hare': 0.48437106612284564,
 'hartebeest': 2.487490442906433,
 'hippopotamus': 0.9841154241370191,
 'honeybadger': 0.7578807078837022,
 'hyenaspotted': 0.9024346817214154,
 'hyenastriped': 1.2609753088435385,
 'impala': 1.7642855177576753,
 'insectspider': 0.6647607384847052,
 'jackal': 0.6572898985445218,
 'koribustard': 0.87362960

In [5]:
train_labels = pd.read_csv("KD/train_labels_KD.csv", index_col="seq_id")
train_labels_columns=train_labels.columns

In [6]:
# c = ['seq_id'] + ['c_' + str(i) for i in list(range(1000))] + ['c2_' + str(i) for i in list(range(1000))] + ['c3_' + str(i) for i in list(range(1000))] +['x']
# good_classes = [9,101, 103, 104, 138, 149,269, 271, 272,274,275, 276, 277, 280 ,288,291,
#                 293,290,330, 331, 334, 340,341,342, 343,344, 345,346,347,348,349, 
#                 351, 352,353, 354,361, 362,363, 372, 386, 703,984 ,975, 979]
# imagenet = pd.read_csv("KD/Imagenet_nasnet_SER_S9.csv", index_col="seq_id", names=c)
# imagenet=imagenet[['c_' + str(i) for i in good_classes] + ['c2_' + str(i) for i in good_classes] + ['c3_' + str(i) for i in good_classes]]
# imagenet.to_csv('KD/Imagenet_nasnet_SER_S9_cleanup.csv')


In [7]:
imagenet = pd.concat([pd.read_csv("KD/Imagenet_nasnet_SER_S9_cleanup.csv", index_col="seq_id"), pd.read_csv("KD/Imagenet_SER_S10_cleanup.csv", index_col="seq_id")])


In [8]:
everything_s10 = pd.read_csv("KD/everything_SER_S10.csv", index_col="seq_id_buf")
everything_s10.index.name='seq_id'


In [9]:
everything_S9 = pd.read_csv("everything_merge.csv", index_col="seq_id")


In [10]:
everything_s10['season'] = 10
everything_S9['season'] = 9

In [11]:
everything = pd.concat([everything_S9, everything_s10])


In [12]:
join = everything.join(train_labels, how='left')
join = imagenet.join(join, how='left')

In [13]:
# for model_id in ['pred_model_480_360_v2_as480_img1_', 'pred_model_480_360_v2_as480_img1_','pred_model_480_360_v2_as480_img1_',
#          'pred_model_480_360_v2_as512_img1_', 'pred_model_480_360_v2_as512_img2_','pred_model_480_360_v2_as512_img3_',
#          'pred_model_480_360_as480_img1_', 'pred_model_480_360_as480_img2_','pred_model_480_360_as480_img3_',
#          'pred_model_480_360_as512_img1_', 'pred_model_480_360_as512_img2_','pred_model_480_360_as512_img3_',
#           'pred_mean_back_2models_as512_','pred_back_as512_']:
#     join[model_id + 'nonempty'] = join[[model_id + c for c in list(train_labels.columns) if c != 'empty']].sum(axis=1)
#     join[model_id + 'maxnonempty'] = join[[model_id + c for c in list(train_labels.columns) if c != 'empty']].max(axis=1)

In [14]:
models = [
            'pred_model_480_360_as512_img',
            'pred_model_480_360_as480_img',
            'pred_model_480_360_v2_as512_img', 
            'pred_model_480_360_v2_as480_img', 
            'pred_model_512_384_v2_as512_img'
         ]
models2 = [
           'pred_mean_back_2models_as512_',
           'pred_mean_back_2models_as480_',
          ]

models3 = [
           'pred_back_as480_',
           'pred_back_as512_',
          ]
# 0.0031143950402571195
# 0.002732702686304169
for c in list(train_labels.columns):
    print(c)
    join['median_img1_' + c] = join[[m + '1_' + c for m in models]].median(axis=1)
    join['median_img2_' + c]=join['median_img1_' + c]
    join['median_img3_' + c]=join['median_img1_' + c]
    join.loc[join.count_imgs > 1, 'median_img2_' + c] = join.loc[join.count_imgs > 1, [m + '2_' + c for m in models]].median(axis=1)
    join.loc[join.count_imgs > 2, 'median_img3_' + c] = join.loc[join.count_imgs > 2, [m + '3_' + c for m in models]].median(axis=1)
    join['mean_imgs_' + c] = (join['median_img1_' + c] + join['median_img2_' + c]*0.8 + join['median_img3_' + c]*0.5) /2.3
    
    join['mean_combines_' + c] = join['mean_imgs_' + c]
    join.loc[join.count_imgs > 1, 'mean_combines_' + c] = join.loc[join.count_imgs > 1,[m  + c for m in models2]].median(axis=1)
    
    join['mean_backs_' + c] = join['mean_imgs_' + c]
    join.loc[join.count_imgs > 1, 'mean_backs_' + c] = join.loc[join.count_imgs > 1,[m  + c for m in models3]].median(axis=1)
    
    join['mean_with_combines_imgs_' + c] = join['mean_imgs_' + c]
    join.loc[join.count_imgs == 2, 'mean_with_combines_imgs_' + c]= join.loc[join.count_imgs == 2,'mean_imgs_' + c]*0.6 + join.loc[join.count_imgs == 2, 'mean_combines_' + c]*0.4
    join.loc[join.count_imgs > 2, 'mean_with_combines_imgs_' + c]= join.loc[join.count_imgs > 2,'mean_imgs_' + c]*0.2 + join.loc[join.count_imgs > 2, 'mean_combines_' + c]*0.8


aardvark


/home/ivan/projects/wildlife/venv/lib/python3.6/site-packages/numpy/lib/nanfunctions.py:1116: RuntimeWarning: All-NaN slice encountered
  overwrite_input=overwrite_input)


aardwolf
baboon
bat
batearedfox
buffalo
bushbuck
caracal
cattle
cheetah
civet
dikdik
duiker
eland
elephant
empty
gazellegrants
gazellethomsons
genet
giraffe
guineafowl
hare
hartebeest
hippopotamus
honeybadger
hyenaspotted
hyenastriped
impala
insectspider
jackal
koribustard
leopard
lionfemale
lionmale
mongoose
monkeyvervet
ostrich
otherbird
porcupine
reedbuck
reptiles
rhinoceros
rodents
secretarybird
serval
steenbok
topi
vulture
warthog
waterbuck
wildcat
wildebeest
zebra
zorilla


In [15]:
DATA_PATH = Path("../../datasets/wildlife") 
train_metadata = pd.read_csv(DATA_PATH / "train_metadata.csv", parse_dates= ['datetime'], index_col="seq_id")
train_metadata = train_metadata.groupby('seq_id').first()
train_metadata['month']=train_metadata.datetime.dt.month
train_metadata['hour']=train_metadata.datetime.dt.hour
join = join.join(train_metadata.hour, how='left')
join = join.join(train_metadata.month, how='left')
join = join.join(train_metadata.datetime, how='left')

In [16]:

join.loc[join.count_imgs<2, ['pred_back_as480_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_back_as512_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_mean_back_2models_as480_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_mean_back_2models_as512_' + c for c in train_labels.columns]]=-0.01

join.loc[join.count_imgs<3, ['pred_model_480_360_as480_img3_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_model_480_360_as480_img2_' + c for c in train_labels.columns]]=-0.01

join.loc[join.count_imgs<3, ['pred_model_480_360_as512_img3_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_model_480_360_as512_img2_' + c for c in train_labels.columns]]=-0.01

join.loc[join.count_imgs<3, ['pred_model_480_360_v2_as480_img3_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_model_480_360_v2_as480_img2_' + c for c in train_labels.columns]]=-0.01

join.loc[join.count_imgs<3, ['pred_model_480_360_v2_as512_img3_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_model_480_360_v2_as512_img2_' + c for c in train_labels.columns]]=-0.01

join.loc[join.count_imgs<3, ['pred_model_512_384_v2_as512_img3_' + c for c in train_labels.columns]]=-0.01
join.loc[join.count_imgs<2, ['pred_model_512_384_v2_as512_img2_' + c for c in train_labels.columns]]=-0.01

           



           

In [17]:
# join['millis'] = join.datetime.astype('int')
# count = join.groupby((join.millis/(10**12)).astype('int'))['empty'].transform('count')-1

# for c in list(train_labels.columns):
#     print(c)
#     field_sum = join.groupby((join.millis/(10**12)).astype('int'))['mean_with_combines_imgs_' + c].transform('sum')
#     join['time_' + c] = (field_sum-join['mean_with_combines_imgs_' + c])/count
#     join.loc[count ==0, 'time_' + c] = -0.01
       

In [18]:

test_index = set(join[join.season==10].index[::2])
test_dataset     = join[join.index.isin(test_index)]
val_dataset = join[(join.season==10) & (~join.index.isin(test_index))]
train_dataset = join[join.season==9]




len(train_dataset), len(val_dataset), len(test_dataset)

(367463, 76660, 76660)

In [25]:
from sklearn.metrics import log_loss
loss = 0
for c in list(train_labels_columns):
#     if c in ['empty', 'wildebeest', 'zebra', 'gazellethomsons', 'buffalo',
# 'elephant', 'hartebeest', 'impala', 'gazellegrants', 'giraffe',
# 'warthog', 'guineafowl', 'otherbird', 'hyenaspotted']:
#         continue
    x = test_dataset[['mean_imgs_' + c, c]].values
    if sum(x[:,1]) !=0:
#         print(c)
        l = log_loss(x[:,1], x[:,0])
        loss+=l
        print(c, l)
print(loss/54)

aardvark 0.00013731720167294877
aardwolf 0.0004617436878763675
baboon 0.0013239710755787544
batearedfox 0.0003168830600818262
buffalo 0.005704100216586983
bushbuck 0.0003142250427602109
caracal 0.00020508034713026378
cattle 0.0006457730831534626
cheetah 0.00047621098861046164
civet 6.16389922841556e-05
dikdik 0.0018127070543624679
duiker 0.0001924839556416757
eland 0.0005580144713067404
elephant 0.004956362592763849
empty 0.04343661125324165
gazellegrants 0.0038933858015273476
gazellethomsons 0.004260466168280168
giraffe 0.0021862861324770276
guineafowl 0.00228757772895913
hare 0.0003088335971532649
hartebeest 0.002185415863551331
hippopotamus 0.0007902843609115818
honeybadger 4.21663199222937e-05
hyenaspotted 0.0011273554741533251
hyenastriped 0.0002814809550501788
impala 0.005687398731226326
insectspider 0.0064539030037461505
jackal 0.0005987367703089405
koribustard 0.0007951841854293885
leopard 0.00021279221130142222
lionfemale 0.0018762954691327449
lionmale 0.0008969065666227006
mo

In [26]:
import gc
del train_metadata
del everything_s10
del everything_S9
del train_labels
del join
gc.collect()

NameError: name 'train_metadata' is not defined

In [27]:
feature_classes=list(train_labels_columns)



feature_classes.remove('reptiles')
feature_classes.remove('caracal')
feature_classes.remove('wildcat')
feature_classes.remove('honeybadger')
feature_classes.remove('vulture')
feature_classes.remove('duiker')
feature_classes.remove('civet')
feature_classes.remove('genet')
feature_classes.remove('rhinoceros')
feature_classes.remove('zorilla')
feature_classes.remove('cattle')
feature_classes.remove('steenbok')
feature_classes.remove('bat')
feature_classes

['aardvark',
 'aardwolf',
 'baboon',
 'batearedfox',
 'buffalo',
 'bushbuck',
 'cheetah',
 'dikdik',
 'eland',
 'elephant',
 'empty',
 'gazellegrants',
 'gazellethomsons',
 'giraffe',
 'guineafowl',
 'hare',
 'hartebeest',
 'hippopotamus',
 'hyenaspotted',
 'hyenastriped',
 'impala',
 'insectspider',
 'jackal',
 'koribustard',
 'leopard',
 'lionfemale',
 'lionmale',
 'mongoose',
 'monkeyvervet',
 'ostrich',
 'otherbird',
 'porcupine',
 'reedbuck',
 'rodents',
 'secretarybird',
 'serval',
 'topi',
 'warthog',
 'waterbuck',
 'wildebeest',
 'zebra']

In [28]:
default_classes = [
        'aardvark', 'aardwolf','baboon','batearedfox','buffalo', 'bushbuck',
 'cheetah', 'dikdik', 'eland', 'elephant', 'empty', 'gazellegrants', 'gazellethomsons',
 'giraffe', 'guineafowl', 'hare', 'hartebeest', 'hippopotamus', 'hyenaspotted', 'hyenastriped',
 'impala', 'insectspider', 'jackal', 'koribustard', 'leopard', 'lionfemale', 'lionmale', 'mongoose',
 'monkeyvervet', 'ostrich', 'otherbird', 'porcupine', 'reedbuck', 'rodents', 'secretarybird', 'serval',
 'topi', 'warthog', 'waterbuck', 'wildebeest', 'zebra']

In [31]:


# feature_classes.append('nonempty')
# feature_classes.append('maxnonempty')
default_classes = [
        'aardvark', 'aardwolf','baboon','batearedfox','buffalo', 'bushbuck',
 'cheetah', 'dikdik', 'eland', 'elephant', 'empty', 'gazellegrants', 'gazellethomsons',
 'giraffe', 'guineafowl', 'hare', 'hartebeest', 'hippopotamus', 'hyenaspotted', 'hyenastriped',
 'impala', 'insectspider', 'jackal', 'koribustard', 'leopard', 'lionfemale', 'lionmale', 'mongoose',
 'monkeyvervet', 'ostrich', 'otherbird', 'porcupine', 'reedbuck', 'rodents', 'secretarybird', 'serval',
 'topi', 'warthog', 'waterbuck', 'wildebeest', 'zebra']

feature_classes_d={
    'zebra':['zebra', 'empty', 'wildebeest','reedbuck', 
                 'gazellethomsons', 'giraffe', 'impala',
                 'koribustard', 'bushbuck'],
    'buffalo':['empty','buffalo', 'wildebeest'],
    'gazellethomsons':['gazellethomsons','empty',  'eland','zebra',
                       'otherbird', 'topi', 'gazellegrants', 'giraffe','lionmale', 'impala'],
    'otherbird':['otherbird', 'empty', 'insectspider', 'dikdik', 'zebra', 'reedbuck'],
    
    'empty':default_classes,
    
        'wildebeest':['zebra', 'empty', 'wildebeest','buffalo', 'gazellethomsons', 'warthog'],
}
    

num_leaves={

}

max_depth={


}
lambda_l1={
    'empty': 0.3,
    'zebra': 0.2,
    'buffalo': 0.3,
}
lambda_l2={
    'empty': 0.3,
    'zebra': 0.2,
    'buffalo': 0.3,
}

learning_rate={
    'zebra':0.008,
#     'empty': 0.008,
}

feature_fraction={
    'zebra':0.5,
    'empty':0.6, #?
}
bagging_fraction={
    'zebra':0.8,
    'empty':0.8, #?
}
bagging_freq={
    'zebra':5,
    'empty':5, #?
}
feature_fraction={
    'zebra':0.6,
    'empty':0.3,
}
# elephant
min_child_samples={
    'empty':30,
    'zebra':30,
    'buffalo':30,
    'topi':30,
    'wildebeest':30,
    'gazellethomsons':30
}

clazz='empty'
feature_classes=feature_classes_d.get(clazz, default_classes)

# columns = ['pred_model_480_360_as480_img1_' + c for c in feature_classes] +\
# ['pred_model_480_360_as480_img2_' + c for c in feature_classes] +\
# ['pred_model_480_360_as480_img3_' + c for c in feature_classes] +\
# ['pred_model_480_360_as512_img1_' + c for c in feature_classes] +\
# ['pred_model_480_360_as512_img2_' + c for c in feature_classes] +\
# ['pred_model_480_360_as512_img3_' + c for c in feature_classes] +\
# ['pred_model_480_360_v2_as480_img1_' + c for c in feature_classes] +\
# ['pred_model_480_360_v2_as480_img2_' + c for c in feature_classes] +\
# ['pred_model_480_360_v2_as480_img3_' + c for c in feature_classes] +\
# ['pred_model_480_360_v2_as512_img1_' + c for c in feature_classes] +\
# ['pred_model_480_360_v2_as512_img2_' + c for c in feature_classes] +\
# ['pred_model_480_360_v2_as512_img3_' + c for c in feature_classes] +\
# ['pred_model_512_384_v2_as512_img1_' + c for c in feature_classes] +\
# ['pred_model_512_384_v2_as512_img2_' + c for c in feature_classes] +\
# ['pred_model_512_384_v2_as512_img3_' + c for c in feature_classes] +\
# ['pred_mean_back_2models_as480_' + c for c in feature_classes] +\
# ['pred_mean_back_2models_as512_' + c for c in feature_classes] +\
# ['pred_back_as480_' + c for c in feature_classes] +\
# ['pred_back_as512_' + c for c in feature_classes] +\
# ['mean_backs_' + c for c in feature_classes] +\
# ['time_' + c for c in feature_classes] +\
# ['median_img1_' + c for c in feature_classes] +\
# ['median_img2_' + c for c in feature_classes] +\
# ['median_img3_' + c for c in feature_classes] +\
# ['mean_combines_' + c for c in feature_classes] +\
# ['mean_with_combines_imgs_' + c for c in feature_classes]+\
# ['c_' + str(i) for i in good_classes] +\
# ['c2_' + str(i) for i in good_classes] +\
# ['c3_' + str(i) for i in good_classes]+\
# ['hour', 'month']


columns = ['pred_model_480_360_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img3_' + c for c in feature_classes] +\
    ['mean_backs_' + c for c in feature_classes] +\
    ['median_img1_' + c for c in feature_classes] +\
    ['median_img2_' + c for c in feature_classes] +\
    ['median_img3_' + c for c in feature_classes] +\
    ['mean_combines_' + c for c in feature_classes] +\
    ['hour', 'month']



In [32]:


# X_train = pd.concat([train_dataset[columns], test_dataset[columns]])
# y_train = pd.concat([train_dataset[clazz], test_dataset[clazz]])
X_train = train_dataset[columns]
y_train = train_dataset[clazz]
X_val = val_dataset[columns]
y_val = val_dataset[clazz]

In [38]:
X_train

pred_model_480_360_as480_img1_aardvark  \
seq_id                                                     
SER_S9#B03#1#1                              0.000000e+00   
SER_S9#B03#1#10                             2.264977e-06   
SER_S9#B03#1#100                            6.258490e-07   
SER_S9#B03#1#101                            0.000000e+00   
SER_S9#B03#1#102                            1.341105e-06   
...                                                  ...   
SER_S9#U11#1#46                             0.000000e+00   
SER_S9#U11#1#5                              2.086160e-07   
SER_S9#U11#1#7                              0.000000e+00   
SER_S9#U11#1#8                              0.000000e+00   
SER_S9#U11#1#9                              0.000000e+00   

                  pred_model_480_360_as480_img1_aardwolf  \
seq_id                                                     
SER_S9#B03#1#1                              0.000000e+00   
SER_S9#B03#1#10                             3.516674e-06   
SER_S9#B03#1#100                            2.384190e-07   
SER_S9#B03#1#101                            0.000000e+00   
SER_S9#B03#1#102                            4.172330e-07   
...                                                  ...   
SER_S9#U11#1#46                             0.000000e+00   
SER_S9#U11#1#5                              2.980230e-07   
SER_S9#U11#1#7                              2.980200e-08   
SER_S9#U11#1#8                              0.000000e+00   
SER_S9#U11#1#9                              0.000000e+00   

                  pred_model_480_360_as480_img1_baboon  \
seq_id                                                   
SER_S9#B03#1#1                            0.000000e+00   
SER_S9#B03#1#10                           4.128337e-03   
SER_S9#B03#1#100                          5.968511e-04   
SER_S9#B03#1#101                          3.537536e-05   
SER_S9#B03#1#102                          1.165152e-03   
...                                                ...   
SER_S9#U11#1#46                           1.102686e-06   
SER_S9#U11#1#5                            5.078316e-05   
SER_S9#U11#1#7                            8.851290e-06   
SER_S9#U11#1#8                            2.235174e-06   
SER_S9#U11#1#9                            1.788140e-07   

                  pred_model_480_360_as480_img1_batearedfox  \
seq_id                                                        
SER_S9#B03#1#1                                 0.000000e+00   
SER_S9#B03#1#10                                4.768372e-06   
SER_S9#B03#1#100                               8.344650e-07   
SER_S9#B03#1#101                               0.000000e+00   
SER_S9#B03#1#102                               1.370907e-06   
...                                                     ...   
SER_S9#U11#1#46                                0.000000e+00   
SER_S9#U11#1#5                                 8.344650e-07   
SER_S9#U11#1#7                                 2.980200e-08   
SER_S9#U11#1#8                                 2.980200e-08   
SER_S9#U11#1#9                                 0.000000e+00   

                  pred_model_480_360_as480_img1_buffalo  \
seq_id                                                    
SER_S9#B03#1#1                             0.000000e+00   
SER_S9#B03#1#10                            8.432567e-04   
SER_S9#B03#1#100                           1.516581e-03   
SER_S9#B03#1#101                           1.347327e-02   
SER_S9#B03#1#102                           2.502948e-03   
...                                                 ...   
SER_S9#U11#1#46                            6.347895e-06   
SER_S9#U11#1#5                             5.403757e-04   
SER_S9#U11#1#7                             6.917119e-05   
SER_S9#U11#1#8                             1.141429e-05   
SER_S9#U11#1#9                             3.278260e-07   

                  pred_model_480_360_as480_img1_bushbuck  \
seq_id                                               

In [39]:
X_val

pred_model_480_360_as480_img1_aardvark  \
seq_id                                                      
SER_S10#B03#1#10                             1.490120e-07   
SER_S10#B03#1#101                            2.980230e-07   
SER_S10#B03#1#103                            2.384190e-07   
SER_S10#B03#1#105                            1.490120e-07   
SER_S10#B03#1#107                            0.000000e+00   
...                                                   ...   
SER_S10#L10#2#151                            0.000000e+00   
SER_S10#L10#2#153                            0.000000e+00   
SER_S10#L10#2#155                            1.788140e-07   
SER_S10#L10#2#157                            3.367662e-06   
SER_S10#L10#2#159                            3.516674e-06   

                   pred_model_480_360_as480_img1_aardwolf  \
seq_id                                                      
SER_S10#B03#1#10                             5.960500e-08   
SER_S10#B03#1#101                            8.940700e-08   
SER_S10#B03#1#103                            5.960500e-08   
SER_S10#B03#1#105                            0.000000e+00   
SER_S10#B03#1#107                            0.000000e+00   
...                                                   ...   
SER_S10#L10#2#151                            0.000000e+00   
SER_S10#L10#2#153                            0.000000e+00   
SER_S10#L10#2#155                            0.000000e+00   
SER_S10#L10#2#157                            2.115965e-06   
SER_S10#L10#2#159                            2.264977e-06   

                   pred_model_480_360_as480_img1_baboon  \
seq_id                                                    
SER_S10#B03#1#10                           6.015122e-03   
SER_S10#B03#1#101                          6.982386e-04   
SER_S10#B03#1#103                          6.828308e-04   
SER_S10#B03#1#105                          1.519918e-06   
SER_S10#B03#1#107                          9.536740e-07   
...                                                 ...   
SER_S10#L10#2#151                          1.192090e-07   
SER_S10#L10#2#153                          1.788140e-07   
SER_S10#L10#2#155                          8.732080e-06   
SER_S10#L10#2#157                          1.433492e-05   
SER_S10#L10#2#159                          1.293421e-05   

                   pred_model_480_360_as480_img1_batearedfox  \
seq_id                                                         
SER_S10#B03#1#10                                3.576280e-07   
SER_S10#B03#1#101                               3.874300e-07   
SER_S10#B03#1#103                               4.172330e-07   
SER_S10#B03#1#105                               5.960500e-08   
SER_S10#B03#1#107                               0.000000e+00   
...                                                      ...   
SER_S10#L10#2#151                               0.000000e+00   
SER_S10#L10#2#153                               0.000000e+00   
SER_S10#L10#2#155                               5.960500e-08   
SER_S10#L10#2#157                               1.293421e-05   
SER_S10#L10#2#159                               7.808208e-06   

                   pred_model_480_360_as480_img1_buffalo  \
seq_id                                                     
SER_S10#B03#1#10                                0.007721   
SER_S10#B03#1#101                               0.001766   
SER_S10#B03#1#103                               0.002099   
SER_S10#B03#1#105                               0.000020   
SER_S10#B03#1#107                               0.000012   
...                                                  ...   
SER_S10#L10#2#151                               0.000001   
SER_S10#L10#2#153                               0.000002   
SER_S10#L10#2#155                               0.000042   
SER_S10#L10#2#157                               0.000160   
SER_S10#L10#2#159                               0.000188   

                   pred_model_480_360_as480_img1_

In [40]:
y_train

seq_id
SER_S9#B03#1#1      1.0
SER_S9#B03#1#10     1.0
SER_S9#B03#1#100    1.0
SER_S9#B03#1#101    0.0
SER_S9#B03#1#102    1.0
                   ... 
SER_S9#U11#1#46     1.0
SER_S9#U11#1#5      1.0
SER_S9#U11#1#7      0.0
SER_S9#U11#1#8      1.0
SER_S9#U11#1#9      1.0
Name: empty, Length: 367463, dtype: float64

In [33]:
y_train.mean()


0.7856954305603557

In [34]:
y_val.mean()/y_train.mean()


1.0196174763260708

In [37]:
scale_pos_weight['empty']

0.9671013291147392

In [36]:


lgb_train = lgb.Dataset(X_train, y_train)
lgb_val = lgb.Dataset(X_val, y_val, reference=lgb_train)

scale = y_train.mean()
print(clazz, math.log(1/scale))
params = {
            'boosting_type': 'gbdt',
            'objective': 'binary',
            'metric': {'binary_logloss'},
            'num_leaves': num_leaves.get(clazz, 32),
            'max_depth': max_depth.get(clazz, 6),
            'learning_rate': learning_rate.get(clazz, 0.01),
            'feature_fraction':  feature_fraction.get(clazz, 0.6),
            'bagging_fraction': bagging_fraction.get(clazz, 0.8),
            'bagging_freq': bagging_freq.get(clazz, 5),
            'verbose': 0,
            'scale_pos_weight':scale_pos_weight.get(clazz, 1),
            'lambda_l1':lambda_l1.get(clazz, 0.2),
            'lambda_l2':lambda_l2.get(clazz, 0.2),
            'min_child_samples':min_child_samples.get(clazz, 20),
#     'max_bins':500

}


gbm = lgb.train(params,
                    lgb_train,
                    num_boost_round=1000,
                    valid_sets=[lgb_train, lgb_val],
                    early_stopping_rounds=20)
gbm.save_model("lgbs_v5/" + clazz + '.txt', num_iteration=gbm.best_iteration) 

X_test = test_dataset[columns]
y_test = test_dataset[clazz]

print(clazz, log_loss(y_test, gbm.predict(X_test.values)))



empty 0.2411860545734701
[1]	training's binary_logloss: 0.510177	valid_1's binary_logloss: 0.490613
Training until validation scores don't improve for 20 rounds
[2]	training's binary_logloss: 0.501105	valid_1's binary_logloss: 0.481993
[3]	training's binary_logloss: 0.492371	valid_1's binary_logloss: 0.473689
[4]	training's binary_logloss: 0.483944	valid_1's binary_logloss: 0.465668
[5]	training's binary_logloss: 0.475846	valid_1's binary_logloss: 0.457935
[6]	training's binary_logloss: 0.467977	valid_1's binary_logloss: 0.450441
[7]	training's binary_logloss: 0.460393	valid_1's binary_logloss: 0.443195
[8]	training's binary_logloss: 0.453055	valid_1's binary_logloss: 0.436197
[9]	training's binary_logloss: 0.445974	valid_1's binary_logloss: 0.429425
[10]	training's binary_logloss: 0.439032	valid_1's binary_logloss: 0.422821
[11]	training's binary_logloss: 0.432354	valid_1's binary_logloss: 0.416432
[12]	training's binary_logloss: 0.425833	valid_1's binary_logloss: 0.41022
[13]	trainin

[109]	training's binary_logloss: 0.144208	valid_1's binary_logloss: 0.140209
[110]	training's binary_logloss: 0.142904	valid_1's binary_logloss: 0.138955
[111]	training's binary_logloss: 0.141614	valid_1's binary_logloss: 0.13772
[112]	training's binary_logloss: 0.140339	valid_1's binary_logloss: 0.136497
[113]	training's binary_logloss: 0.139097	valid_1's binary_logloss: 0.135299
[114]	training's binary_logloss: 0.137907	valid_1's binary_logloss: 0.134154
[115]	training's binary_logloss: 0.13668	valid_1's binary_logloss: 0.132973
[116]	training's binary_logloss: 0.135476	valid_1's binary_logloss: 0.131815
[117]	training's binary_logloss: 0.134282	valid_1's binary_logloss: 0.130666
[118]	training's binary_logloss: 0.1331	valid_1's binary_logloss: 0.129527
[119]	training's binary_logloss: 0.131933	valid_1's binary_logloss: 0.128407
[120]	training's binary_logloss: 0.130779	valid_1's binary_logloss: 0.127299
[121]	training's binary_logloss: 0.129638	valid_1's binary_logloss: 0.126201
[12

[215]	training's binary_logloss: 0.0648792	valid_1's binary_logloss: 0.0642754
[216]	training's binary_logloss: 0.0644901	valid_1's binary_logloss: 0.0639
[217]	training's binary_logloss: 0.0641062	valid_1's binary_logloss: 0.063536
[218]	training's binary_logloss: 0.0637263	valid_1's binary_logloss: 0.06317
[219]	training's binary_logloss: 0.06335	valid_1's binary_logloss: 0.0628158
[220]	training's binary_logloss: 0.0629721	valid_1's binary_logloss: 0.0624571
[221]	training's binary_logloss: 0.0626101	valid_1's binary_logloss: 0.0621212
[222]	training's binary_logloss: 0.0622443	valid_1's binary_logloss: 0.0617756
[223]	training's binary_logloss: 0.0618775	valid_1's binary_logloss: 0.0614245
[224]	training's binary_logloss: 0.0615254	valid_1's binary_logloss: 0.0610924
[225]	training's binary_logloss: 0.0611653	valid_1's binary_logloss: 0.0607546
[226]	training's binary_logloss: 0.060809	valid_1's binary_logloss: 0.0604235
[227]	training's binary_logloss: 0.0604555	valid_1's binary_l

[321]	training's binary_logloss: 0.0395677	valid_1's binary_logloss: 0.0407795
[322]	training's binary_logloss: 0.0394424	valid_1's binary_logloss: 0.0406676
[323]	training's binary_logloss: 0.0393101	valid_1's binary_logloss: 0.0405522
[324]	training's binary_logloss: 0.0391776	valid_1's binary_logloss: 0.0404368
[325]	training's binary_logloss: 0.0390471	valid_1's binary_logloss: 0.0403193
[326]	training's binary_logloss: 0.0389178	valid_1's binary_logloss: 0.0402051
[327]	training's binary_logloss: 0.0387875	valid_1's binary_logloss: 0.0400954
[328]	training's binary_logloss: 0.0386609	valid_1's binary_logloss: 0.039978
[329]	training's binary_logloss: 0.0385363	valid_1's binary_logloss: 0.039863
[330]	training's binary_logloss: 0.0384125	valid_1's binary_logloss: 0.0397501
[331]	training's binary_logloss: 0.0382897	valid_1's binary_logloss: 0.0396366
[332]	training's binary_logloss: 0.0381734	valid_1's binary_logloss: 0.0395313
[333]	training's binary_logloss: 0.0380517	valid_1's b

[426]	training's binary_logloss: 0.0306187	valid_1's binary_logloss: 0.0331805
[427]	training's binary_logloss: 0.0305667	valid_1's binary_logloss: 0.0331412
[428]	training's binary_logloss: 0.0305159	valid_1's binary_logloss: 0.0331083
[429]	training's binary_logloss: 0.0304658	valid_1's binary_logloss: 0.03307
[430]	training's binary_logloss: 0.030415	valid_1's binary_logloss: 0.0330351
[431]	training's binary_logloss: 0.0303651	valid_1's binary_logloss: 0.0329985
[432]	training's binary_logloss: 0.0303154	valid_1's binary_logloss: 0.0329633
[433]	training's binary_logloss: 0.0302679	valid_1's binary_logloss: 0.0329258
[434]	training's binary_logloss: 0.0302208	valid_1's binary_logloss: 0.0328928
[435]	training's binary_logloss: 0.0301746	valid_1's binary_logloss: 0.0328555
[436]	training's binary_logloss: 0.0301278	valid_1's binary_logloss: 0.0328193
[437]	training's binary_logloss: 0.0300837	valid_1's binary_logloss: 0.0327856
[438]	training's binary_logloss: 0.030037	valid_1's bin

[531]	training's binary_logloss: 0.0270522	valid_1's binary_logloss: 0.0307311
[532]	training's binary_logloss: 0.0270254	valid_1's binary_logloss: 0.0307155
[533]	training's binary_logloss: 0.0270017	valid_1's binary_logloss: 0.0307034
[534]	training's binary_logloss: 0.0269806	valid_1's binary_logloss: 0.0306928
[535]	training's binary_logloss: 0.0269592	valid_1's binary_logloss: 0.03068
[536]	training's binary_logloss: 0.0269384	valid_1's binary_logloss: 0.030668
[537]	training's binary_logloss: 0.0269164	valid_1's binary_logloss: 0.0306525
[538]	training's binary_logloss: 0.0268942	valid_1's binary_logloss: 0.0306399
[539]	training's binary_logloss: 0.0268762	valid_1's binary_logloss: 0.0306302
[540]	training's binary_logloss: 0.0268562	valid_1's binary_logloss: 0.0306205
[541]	training's binary_logloss: 0.0268352	valid_1's binary_logloss: 0.0306075
[542]	training's binary_logloss: 0.0268148	valid_1's binary_logloss: 0.0305963
[543]	training's binary_logloss: 0.0267952	valid_1's bi

[636]	training's binary_logloss: 0.0252831	valid_1's binary_logloss: 0.0300091
[637]	training's binary_logloss: 0.0252734	valid_1's binary_logloss: 0.0300068
[638]	training's binary_logloss: 0.0252611	valid_1's binary_logloss: 0.0300063
[639]	training's binary_logloss: 0.0252482	valid_1's binary_logloss: 0.0300014
[640]	training's binary_logloss: 0.0252361	valid_1's binary_logloss: 0.0299987
[641]	training's binary_logloss: 0.0252253	valid_1's binary_logloss: 0.0299948
[642]	training's binary_logloss: 0.0252136	valid_1's binary_logloss: 0.0299872
[643]	training's binary_logloss: 0.0252017	valid_1's binary_logloss: 0.0299864
[644]	training's binary_logloss: 0.0251899	valid_1's binary_logloss: 0.0299844
[645]	training's binary_logloss: 0.0251789	valid_1's binary_logloss: 0.0299822
[646]	training's binary_logloss: 0.0251704	valid_1's binary_logloss: 0.0299808
[647]	training's binary_logloss: 0.0251591	valid_1's binary_logloss: 0.0299755
[648]	training's binary_logloss: 0.0251491	valid_1's

KeyboardInterrupt: 

In [33]:
X_test = test_dataset[columns]
y_test = test_dataset[clazz]
X_test[['time_' + c for c in feature_classes]]=-0.01
print(clazz, log_loss(y_test, gbm.predict(X_test.values)))

/home/ivan/projects/wildlife/venv/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/home/ivan/projects/wildlife/venv/lib/python3.6/site-packages/pandas/core/indexing.py:494: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


elephant 0.004232378804765939


In [142]:
import gc
gc.collect()

39

In [113]:
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)

feature_imp = pd.DataFrame(sorted(zip(gbm.feature_importance(),X_test.columns)), columns=['Value','Feature'])
feature_imp[-100:]


Value                                        Feature
1384     17                                time_wildebeest
1385     18                                         c2_269
1386     18                                         c2_272
1387     18                                         c3_340
1388     18                                         c3_984
1389     18                           mean_combines_baboon
1390     18                 mean_with_combines_imgs_baboon
1391     18                           median_img3_lionmale
1392     18        pred_model_480_360_as480_img3_otherbird
1393     18  pred_model_512_384_v2_as512_img2_hippopotamus
1394     18                                   time_zorilla
1395     19                                         c3_101
1396     19                                         c3_272
1397     19                                         c3_288
1398     19                                         c3_386
1399     19                                          c_149
1400     19                                          c_272
1401     19                         pred_back_as512_impala
1402     19      pred_mean_back_2models_as512_insectspider
1403     19            pred_model_480_360_as512_img2_empty
1404     19       pred_model_512_384_v2_as512_img3_ostrich
1405     20                                         c3_103
1406     20                                          c_277
1407     20             mean_with_combines_imgs_guineafowl
1408     20                          pred_back_as480_empty
1409     20                        pred_back_as512_giraffe
1410     20                                  time_reptiles
1411     21                                         c2_354
1412     21                                         c2_361
1413     21                                          c_979
1414     21               mean_with_combines_imgs_elephant
1415     21            pred_mean_back_2models_as512_baboon
1416     21           pred_model_480_360_as480_img2_baboon
1417     21     pred_model_480_360_as480_img2_insectspider
1418     22                                          c_975
1419     22     pred_model_480_360_v2_as512_img3_otherbird
1420     22                                   time_giraffe
1421     22                                time_hartebeest
1422     22                               time_koribustard
1423     23                                         c3_703
1424     23                           mean_combines_impala
1425     23                     mean_combines_insectspider
1426     23         pred_mean_back_2models_as480_otherbird
1427     23         pred_model_512_384_v2_as512_img1_empty
1428     23                                       time_bat
1429     24                                         c2_984
1430     24                       median_img2_insectspider
1431     24              pred_mean_back_2models_as512_hare
1432     24     pred_model_480_360_v2_as480_img2_otherbird
1433     24  pred_model_512_384_v2_as512_img2_insectspider
1434     24                                    time_serval
1435     25                                          c_341
1436     25                           pred_back_as480_hare
1437     25                                  time_mongoose
1438     26                     pred_back_as480_guineafowl
1439     27                                         c2_347
1440     27                                          c_293
1441     27            pred_mean_back_2models_as480_impala
1442     27                              time_hyenastriped
1443     27                              time_insectspider
1444     28                                          c_361
1445     28                       pred_back_as480_reptiles
1446     28       pred_model_512_384_v2_as512_img3_giraffe
1447     28                                time_guineafowl
1448     28                                 time_otherbird
1449     29                                         c3_354
1450     31                                         c

In [23]:
clazzs = ['empty', 'wildebeest', 'zebra', 'gazellethomsons', 'buffalo',
'elephant', 'hartebeest', 'impala', 'gazellegrants', 'giraffe',
'warthog', 'guineafowl', 'otherbird', 'hyenaspotted', 'lionfemale', 
'eland', 'hippopotamus', 'reedbuck', 'topi', 'baboon', 'dikdik', 
'secretarybird', 'jackal']

for clazz in clazzs:
    
#     feature_classes=feature_classes_d.get(clazz, list(train_labels_columns))
    feature_classes=default_classes

    columns = ['pred_model_480_360_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_mean_back_2models_as480_' + c for c in feature_classes] +\
    ['pred_mean_back_2models_as512_' + c for c in feature_classes] +\
    ['mean_backs_' + c for c in feature_classes] +\
    ['median_img1_' + c for c in feature_classes] +\
    ['median_img2_' + c for c in feature_classes] +\
    ['median_img3_' + c for c in feature_classes] +\
    ['mean_combines_' + c for c in feature_classes] +\
    ['c_' + str(i) for i in good_classes] +\
    ['c2_' + str(i) for i in good_classes] +\
    ['c3_' + str(i) for i in good_classes]+\
    ['hour', 'month']



    X_train = train_dataset[columns]
    y_train = train_dataset[clazz]
    X_val = val_dataset[columns]
    y_val = val_dataset[clazz]

    lgb_train = lgb.Dataset(X_train, y_train)
    lgb_val = lgb.Dataset(X_val, y_val, reference=lgb_train)

    params = {
                'boosting_type': 'gbdt',
                'objective': 'binary',
                'metric': {'binary_logloss'},
                'num_leaves': num_leaves.get(clazz, 32),
                'max_depth': max_depth.get(clazz, 6),
                'learning_rate': learning_rate.get(clazz, 0.01),
                'feature_fraction':  feature_fraction.get(clazz, 0.6),
                'bagging_fraction': bagging_fraction.get(clazz, 0.8),
                'bagging_freq': bagging_freq.get(clazz, 5),
                'scale_pos_weight':scale_pos_weight.get(clazz, 1),
                'lambda_l1':lambda_l1.get(clazz, 0.2),
                'lambda_l2':lambda_l2.get(clazz, 0.2),
                'min_child_samples':min_child_samples.get(clazz, 25),

    }

    gbm = lgb.train(params,
                        lgb_train,
                        num_boost_round=3000,
                        valid_sets=[lgb_train, lgb_val],
                        early_stopping_rounds=20)
    gbm.save_model("lgbs_v5/" + clazz + '.txt', num_iteration=gbm.best_iteration) 

    X_test = test_dataset[columns]
    y_test = test_dataset[clazz]

    print(clazz, log_loss(y_test, gbm.predict(X_test.values)))

0.2411860545734701
[1]	training's binary_logloss: 0.510177	valid_1's binary_logloss: 0.490621
Training until validation scores don't improve for 20 rounds
[2]	training's binary_logloss: 0.501119	valid_1's binary_logloss: 0.482004
[3]	training's binary_logloss: 0.492386	valid_1's binary_logloss: 0.473696
[4]	training's binary_logloss: 0.483974	valid_1's binary_logloss: 0.465688
[5]	training's binary_logloss: 0.475886	valid_1's binary_logloss: 0.457988
[6]	training's binary_logloss: 0.468021	valid_1's binary_logloss: 0.45049
[7]	training's binary_logloss: 0.460405	valid_1's binary_logloss: 0.443226
[8]	training's binary_logloss: 0.453019	valid_1's binary_logloss: 0.436189
[9]	training's binary_logloss: 0.445858	valid_1's binary_logloss: 0.429371
[10]	training's binary_logloss: 0.43891	valid_1's binary_logloss: 0.422754
[11]	training's binary_logloss: 0.432207	valid_1's binary_logloss: 0.416356
[12]	training's binary_logloss: 0.42566	valid_1's binary_logloss: 0.410115
[13]	training's bina

[109]	training's binary_logloss: 0.143814	valid_1's binary_logloss: 0.139995
[110]	training's binary_logloss: 0.142516	valid_1's binary_logloss: 0.138752
[111]	training's binary_logloss: 0.141231	valid_1's binary_logloss: 0.137515
[112]	training's binary_logloss: 0.139963	valid_1's binary_logloss: 0.136301
[113]	training's binary_logloss: 0.138717	valid_1's binary_logloss: 0.135108
[114]	training's binary_logloss: 0.137494	valid_1's binary_logloss: 0.133928
[115]	training's binary_logloss: 0.136277	valid_1's binary_logloss: 0.132751
[116]	training's binary_logloss: 0.13507	valid_1's binary_logloss: 0.131595
[117]	training's binary_logloss: 0.133884	valid_1's binary_logloss: 0.130446
[118]	training's binary_logloss: 0.132714	valid_1's binary_logloss: 0.129321
[119]	training's binary_logloss: 0.131553	valid_1's binary_logloss: 0.128205
[120]	training's binary_logloss: 0.130403	valid_1's binary_logloss: 0.1271
[121]	training's binary_logloss: 0.129272	valid_1's binary_logloss: 0.126016
[1

[216]	training's binary_logloss: 0.0642067	valid_1's binary_logloss: 0.0638611
[217]	training's binary_logloss: 0.0638234	valid_1's binary_logloss: 0.0635017
[218]	training's binary_logloss: 0.0634421	valid_1's binary_logloss: 0.063143
[219]	training's binary_logloss: 0.0630644	valid_1's binary_logloss: 0.0627895
[220]	training's binary_logloss: 0.062687	valid_1's binary_logloss: 0.0624345
[221]	training's binary_logloss: 0.0623173	valid_1's binary_logloss: 0.0620946
[222]	training's binary_logloss: 0.0619482	valid_1's binary_logloss: 0.0617522
[223]	training's binary_logloss: 0.0615858	valid_1's binary_logloss: 0.0614096
[224]	training's binary_logloss: 0.0612274	valid_1's binary_logloss: 0.061074
[225]	training's binary_logloss: 0.060872	valid_1's binary_logloss: 0.0607468
[226]	training's binary_logloss: 0.0605196	valid_1's binary_logloss: 0.0604156
[227]	training's binary_logloss: 0.0601697	valid_1's binary_logloss: 0.0600858
[228]	training's binary_logloss: 0.0598233	valid_1's bin

[322]	training's binary_logloss: 0.0392194	valid_1's binary_logloss: 0.0408468
[323]	training's binary_logloss: 0.03909	valid_1's binary_logloss: 0.0407346
[324]	training's binary_logloss: 0.0389593	valid_1's binary_logloss: 0.0406255
[325]	training's binary_logloss: 0.0388294	valid_1's binary_logloss: 0.0405181
[326]	training's binary_logloss: 0.0386986	valid_1's binary_logloss: 0.0404046
[327]	training's binary_logloss: 0.0385801	valid_1's binary_logloss: 0.0403075
[328]	training's binary_logloss: 0.0384541	valid_1's binary_logloss: 0.0401927
[329]	training's binary_logloss: 0.0383314	valid_1's binary_logloss: 0.0400877
[330]	training's binary_logloss: 0.0382078	valid_1's binary_logloss: 0.0399851
[331]	training's binary_logloss: 0.0380842	valid_1's binary_logloss: 0.0398761
[332]	training's binary_logloss: 0.0379652	valid_1's binary_logloss: 0.0397714
[333]	training's binary_logloss: 0.0378427	valid_1's binary_logloss: 0.0396699
[334]	training's binary_logloss: 0.0377228	valid_1's b

[426]	training's binary_logloss: 0.0304323	valid_1's binary_logloss: 0.0334882
[427]	training's binary_logloss: 0.0303803	valid_1's binary_logloss: 0.0334467
[428]	training's binary_logloss: 0.0303299	valid_1's binary_logloss: 0.0334095
[429]	training's binary_logloss: 0.0302832	valid_1's binary_logloss: 0.0333717
[430]	training's binary_logloss: 0.0302359	valid_1's binary_logloss: 0.0333342
[431]	training's binary_logloss: 0.0301852	valid_1's binary_logloss: 0.0332966
[432]	training's binary_logloss: 0.0301349	valid_1's binary_logloss: 0.0332565
[433]	training's binary_logloss: 0.0300852	valid_1's binary_logloss: 0.0332173
[434]	training's binary_logloss: 0.0300425	valid_1's binary_logloss: 0.0331849
[435]	training's binary_logloss: 0.0299957	valid_1's binary_logloss: 0.0331448
[436]	training's binary_logloss: 0.0299482	valid_1's binary_logloss: 0.0331077
[437]	training's binary_logloss: 0.029901	valid_1's binary_logloss: 0.0330723
[438]	training's binary_logloss: 0.0298579	valid_1's 

...

[205]	training's binary_logloss: 0.000103127	valid_1's binary_logloss: 0.000370562
[206]	training's binary_logloss: 0.000102247	valid_1's binary_logloss: 0.00036979
[207]	training's binary_logloss: 0.000101422	valid_1's binary_logloss: 0.00036915
[208]	training's binary_logloss: 0.000100602	valid_1's binary_logloss: 0.000368479
[209]	training's binary_logloss: 9.97957e-05	valid_1's binary_logloss: 0.000367857
[210]	training's binary_logloss: 9.89402e-05	valid_1's binary_logloss: 0.000367493
[211]	training's binary_logloss: 9.81e-05	valid_1's binary_logloss: 0.000366906
[212]	training's binary_logloss: 9.72896e-05	valid_1's binary_logloss: 0.000366455
[213]	training's binary_logloss: 9.64721e-05	valid_1's binary_logloss: 0.000365887
[214]	training's binary_logloss: 9.56822e-05	valid_1's binary_logloss: 0.000365329
[215]	training's binary_logloss: 9.4901e-05	valid_1's binary_logloss: 0.000364607
[216]	training's binary_logloss: 9.42255e-05	valid_1's binary_logloss: 0.000364308
[217]	trai

[304]	training's binary_logloss: 4.9474e-05	valid_1's binary_logloss: 0.000341655
[305]	training's binary_logloss: 4.91256e-05	valid_1's binary_logloss: 0.000341593
[306]	training's binary_logloss: 4.87628e-05	valid_1's binary_logloss: 0.000341677
[307]	training's binary_logloss: 4.84211e-05	valid_1's binary_logloss: 0.000341466
[308]	training's binary_logloss: 4.81142e-05	valid_1's binary_logloss: 0.000341415
[309]	training's binary_logloss: 4.77853e-05	valid_1's binary_logloss: 0.000341458
[310]	training's binary_logloss: 4.74327e-05	valid_1's binary_logloss: 0.000341431
[311]	training's binary_logloss: 4.71653e-05	valid_1's binary_logloss: 0.000341482
[312]	training's binary_logloss: 4.68849e-05	valid_1's binary_logloss: 0.000341298
[313]	training's binary_logloss: 4.66251e-05	valid_1's binary_logloss: 0.000341358
[314]	training's binary_logloss: 4.63543e-05	valid_1's binary_logloss: 0.000341182
[315]	training's binary_logloss: 4.60997e-05	valid_1's binary_logloss: 0.000341244
[316]

[1]	training's binary_logloss: 0.00367883	valid_1's binary_logloss: 0.00707962
Training until validation scores don't improve for 20 rounds
[2]	training's binary_logloss: 0.00349761	valid_1's binary_logloss: 0.00699775
[3]	training's binary_logloss: 0.00336521	valid_1's binary_logloss: 0.00685884
[4]	training's binary_logloss: 0.00326052	valid_1's binary_logloss: 0.00675292
[5]	training's binary_logloss: 0.00316895	valid_1's binary_logloss: 0.0066796
[6]	training's binary_logloss: 0.00307975	valid_1's binary_logloss: 0.0065775
[7]	training's binary_logloss: 0.00298884	valid_1's binary_logloss: 0.00652759
[8]	training's binary_logloss: 0.00291746	valid_1's binary_logloss: 0.00648701
[9]	training's binary_logloss: 0.00283615	valid_1's binary_logloss: 0.00644783
[10]	training's binary_logloss: 0.00277097	valid_1's binary_logloss: 0.00639144
[11]	training's binary_logloss: 0.00270968	valid_1's binary_logloss: 0.00635082
[12]	training's binary_logloss: 0.00265916	valid_1's binary_logloss: 0

[104]	training's binary_logloss: 0.00110843	valid_1's binary_logloss: 0.00560316
[105]	training's binary_logloss: 0.00110247	valid_1's binary_logloss: 0.00560204
[106]	training's binary_logloss: 0.00109601	valid_1's binary_logloss: 0.00559988
[107]	training's binary_logloss: 0.00108935	valid_1's binary_logloss: 0.0055973
[108]	training's binary_logloss: 0.001083	valid_1's binary_logloss: 0.00559493
[109]	training's binary_logloss: 0.00107563	valid_1's binary_logloss: 0.00559301
[110]	training's binary_logloss: 0.0010687	valid_1's binary_logloss: 0.00559162
[111]	training's binary_logloss: 0.00106233	valid_1's binary_logloss: 0.00559075
[112]	training's binary_logloss: 0.0010552	valid_1's binary_logloss: 0.00559126
[113]	training's binary_logloss: 0.00104826	valid_1's binary_logloss: 0.00559318
[114]	training's binary_logloss: 0.00104152	valid_1's binary_logloss: 0.00559193
[115]	training's binary_logloss: 0.00103484	valid_1's binary_logloss: 0.00559263
[116]	training's binary_logloss: 

KeyboardInterrupt: 

In [24]:
clazzs = ['empty', 'wildebeest', 'zebra', 'gazellethomsons', 'buffalo',
'elephant', 'hartebeest', 'impala', 'gazellegrants', 'giraffe',
'warthog', 'guineafowl', 'otherbird', 'hyenaspotted', 'lionfemale', 
'eland', 'hippopotamus', 'reedbuck', 'topi', 'baboon', 'dikdik', 
'secretarybird', 'jackal']

[   
 
    'lionfemale', 
'eland', 'hippopotamus', 'reedbuck', 'topi', 'baboon', 'dikdik', 
'secretarybird', 'jackal']

'baboon', 'hare',   'honeybadger', 'insectspider', 'mongoose',

        
for clazz in clazzs:
    
#     feature_classes=feature_classes_d.get(clazz, list(train_labels_columns))
    feature_classes=default_classes

    columns = ['pred_model_480_360_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_mean_back_2models_as480_' + c for c in feature_classes] +\
    ['pred_mean_back_2models_as512_' + c for c in feature_classes] +\
    ['mean_backs_' + c for c in feature_classes] +\
    ['median_img1_' + c for c in feature_classes] +\
    ['median_img2_' + c for c in feature_classes] +\
    ['median_img3_' + c for c in feature_classes] +\
    ['mean_combines_' + c for c in feature_classes] +\
    ['c_' + str(i) for i in good_classes] +\
    ['c2_' + str(i) for i in good_classes] +\
    ['c3_' + str(i) for i in good_classes]+\
    ['hour', 'month']



    X_train = train_dataset[columns]
    y_train = train_dataset[clazz]
    X_val = val_dataset[columns]
    y_val = val_dataset[clazz]

    lgb_train = lgb.Dataset(X_train, y_train)
    lgb_val = lgb.Dataset(X_val, y_val, reference=lgb_train)

    params = {
                'boosting_type': 'gbdt',
                'objective': 'binary',
                'metric': {'binary_logloss'},
                'num_leaves': num_leaves.get(clazz, 32),
                'max_depth': max_depth.get(clazz, 6),
                'learning_rate': learning_rate.get(clazz, 0.01),
                'feature_fraction':  feature_fraction.get(clazz, 0.6),
                'bagging_fraction': bagging_fraction.get(clazz, 0.8),
                'bagging_freq': bagging_freq.get(clazz, 5),
                'scale_pos_weight':scale_pos_weight.get(clazz, 1),
                'lambda_l1':lambda_l1.get(clazz, 0.2),
                'lambda_l2':lambda_l2.get(clazz, 0.2),
                'min_child_samples':min_child_samples.get(clazz, 25),

    }

    gbm = lgb.train(params,
                        lgb_train,
                        num_boost_round=3000,
                        valid_sets=[lgb_train, lgb_val],
                        early_stopping_rounds=40)
    gbm.save_model("lgbs_v6/" + clazz + '.txt', num_iteration=gbm.best_iteration) 

    X_test = test_dataset[columns]
    y_test = test_dataset[clazz]

    print(clazz, log_loss(y_test, gbm.predict(X_test.values)))

[1]	training's binary_logloss: 0.510177	valid_1's binary_logloss: 0.490621
Training until validation scores don't improve for 20 rounds
[2]	training's binary_logloss: 0.501119	valid_1's binary_logloss: 0.482004
[3]	training's binary_logloss: 0.492386	valid_1's binary_logloss: 0.473696
[4]	training's binary_logloss: 0.483974	valid_1's binary_logloss: 0.465688
[5]	training's binary_logloss: 0.475886	valid_1's binary_logloss: 0.457988
[6]	training's binary_logloss: 0.468021	valid_1's binary_logloss: 0.45049
[7]	training's binary_logloss: 0.460405	valid_1's binary_logloss: 0.443226
[8]	training's binary_logloss: 0.453019	valid_1's binary_logloss: 0.436189
[9]	training's binary_logloss: 0.445858	valid_1's binary_logloss: 0.429371
[10]	training's binary_logloss: 0.43891	valid_1's binary_logloss: 0.422754
[11]	training's binary_logloss: 0.432207	valid_1's binary_logloss: 0.416356
[12]	training's binary_logloss: 0.42566	valid_1's binary_logloss: 0.410115
[13]	training's binary_logloss: 0.41934

[109]	training's binary_logloss: 0.143814	valid_1's binary_logloss: 0.139995
[110]	training's binary_logloss: 0.142516	valid_1's binary_logloss: 0.138752
[111]	training's binary_logloss: 0.141231	valid_1's binary_logloss: 0.137515
[112]	training's binary_logloss: 0.139963	valid_1's binary_logloss: 0.136301
[113]	training's binary_logloss: 0.138717	valid_1's binary_logloss: 0.135108
[114]	training's binary_logloss: 0.137494	valid_1's binary_logloss: 0.133928
[115]	training's binary_logloss: 0.136277	valid_1's binary_logloss: 0.132751
[116]	training's binary_logloss: 0.13507	valid_1's binary_logloss: 0.131595
[117]	training's binary_logloss: 0.133884	valid_1's binary_logloss: 0.130446
[118]	training's binary_logloss: 0.132714	valid_1's binary_logloss: 0.129321
[119]	training's binary_logloss: 0.131553	valid_1's binary_logloss: 0.128205
[120]	training's binary_logloss: 0.130403	valid_1's binary_logloss: 0.1271
[121]	training's binary_logloss: 0.129272	valid_1's binary_logloss: 0.126016
[1

[216]	training's binary_logloss: 0.0642067	valid_1's binary_logloss: 0.0638611
[217]	training's binary_logloss: 0.0638234	valid_1's binary_logloss: 0.0635017
[218]	training's binary_logloss: 0.0634421	valid_1's binary_logloss: 0.063143
[219]	training's binary_logloss: 0.0630644	valid_1's binary_logloss: 0.0627895
[220]	training's binary_logloss: 0.062687	valid_1's binary_logloss: 0.0624345
[221]	training's binary_logloss: 0.0623173	valid_1's binary_logloss: 0.0620946
[222]	training's binary_logloss: 0.0619482	valid_1's binary_logloss: 0.0617522
[223]	training's binary_logloss: 0.0615858	valid_1's binary_logloss: 0.0614096
[224]	training's binary_logloss: 0.0612274	valid_1's binary_logloss: 0.061074
[225]	training's binary_logloss: 0.060872	valid_1's binary_logloss: 0.0607468
[226]	training's binary_logloss: 0.0605196	valid_1's binary_logloss: 0.0604156
[227]	training's binary_logloss: 0.0601697	valid_1's binary_logloss: 0.0600858
[228]	training's binary_logloss: 0.0598233	valid_1's bin

[322]	training's binary_logloss: 0.0392194	valid_1's binary_logloss: 0.0408468
[323]	training's binary_logloss: 0.03909	valid_1's binary_logloss: 0.0407346
[324]	training's binary_logloss: 0.0389593	valid_1's binary_logloss: 0.0406255
[325]	training's binary_logloss: 0.0388294	valid_1's binary_logloss: 0.0405181
[326]	training's binary_logloss: 0.0386986	valid_1's binary_logloss: 0.0404046
[327]	training's binary_logloss: 0.0385801	valid_1's binary_logloss: 0.0403075
[328]	training's binary_logloss: 0.0384541	valid_1's binary_logloss: 0.0401927
[329]	training's binary_logloss: 0.0383314	valid_1's binary_logloss: 0.0400877
[330]	training's binary_logloss: 0.0382078	valid_1's binary_logloss: 0.0399851
[331]	training's binary_logloss: 0.0380842	valid_1's binary_logloss: 0.0398761
[332]	training's binary_logloss: 0.0379652	valid_1's binary_logloss: 0.0397714
[333]	training's binary_logloss: 0.0378427	valid_1's binary_logloss: 0.0396699
[334]	training's binary_logloss: 0.0377228	valid_1's b

[426]	training's binary_logloss: 0.0304323	valid_1's binary_logloss: 0.0334882
[427]	training's binary_logloss: 0.0303803	valid_1's binary_logloss: 0.0334467
[428]	training's binary_logloss: 0.0303299	valid_1's binary_logloss: 0.0334095
[429]	training's binary_logloss: 0.0302832	valid_1's binary_logloss: 0.0333717
[430]	training's binary_logloss: 0.0302359	valid_1's binary_logloss: 0.0333342
[431]	training's binary_logloss: 0.0301852	valid_1's binary_logloss: 0.0332966
[432]	training's binary_logloss: 0.0301349	valid_1's binary_logloss: 0.0332565
[433]	training's binary_logloss: 0.0300852	valid_1's binary_logloss: 0.0332173
[434]	training's binary_logloss: 0.0300425	valid_1's binary_logloss: 0.0331849
[435]	training's binary_logloss: 0.0299957	valid_1's binary_logloss: 0.0331448
[436]	training's binary_logloss: 0.0299482	valid_1's binary_logloss: 0.0331077
[437]	training's binary_logloss: 0.029901	valid_1's binary_logloss: 0.0330723
[438]	training's binary_logloss: 0.0298579	valid_1's 

...

[173]	training's binary_logloss: 0.0025555	valid_1's binary_logloss: 0.0023616
[174]	training's binary_logloss: 0.00253671	valid_1's binary_logloss: 0.00235075
[175]	training's binary_logloss: 0.00251927	valid_1's binary_logloss: 0.00233966
[176]	training's binary_logloss: 0.00250171	valid_1's binary_logloss: 0.00232892
[177]	training's binary_logloss: 0.00248397	valid_1's binary_logloss: 0.00231808
[178]	training's binary_logloss: 0.00246724	valid_1's binary_logloss: 0.00230693
[179]	training's binary_logloss: 0.00244999	valid_1's binary_logloss: 0.00229706
[180]	training's binary_logloss: 0.0024334	valid_1's binary_logloss: 0.00228597
[181]	training's binary_logloss: 0.00241597	valid_1's binary_logloss: 0.00227454
[182]	training's binary_logloss: 0.00239806	valid_1's binary_logloss: 0.00226412
[183]	training's binary_logloss: 0.00238018	valid_1's binary_logloss: 0.00225383
[184]	training's binary_logloss: 0.0023634	valid_1's binary_logloss: 0.00224402
[185]	training's binary_logloss:

[275]	training's binary_logloss: 0.00137326	valid_1's binary_logloss: 0.0016631
[276]	training's binary_logloss: 0.00136614	valid_1's binary_logloss: 0.00165946
[277]	training's binary_logloss: 0.00135928	valid_1's binary_logloss: 0.00165538
[278]	training's binary_logloss: 0.00135249	valid_1's binary_logloss: 0.00165114
[279]	training's binary_logloss: 0.00134562	valid_1's binary_logloss: 0.00164763
[280]	training's binary_logloss: 0.0013386	valid_1's binary_logloss: 0.00164416
[281]	training's binary_logloss: 0.00133205	valid_1's binary_logloss: 0.00164033
[282]	training's binary_logloss: 0.00132608	valid_1's binary_logloss: 0.00163669
[283]	training's binary_logloss: 0.00131967	valid_1's binary_logloss: 0.00163342
[284]	training's binary_logloss: 0.00131284	valid_1's binary_logloss: 0.00163081
[285]	training's binary_logloss: 0.00130704	valid_1's binary_logloss: 0.00162732
[286]	training's binary_logloss: 0.00130102	valid_1's binary_logloss: 0.00162388
[287]	training's binary_loglos

[377]	training's binary_logloss: 0.000902607	valid_1's binary_logloss: 0.00143555
[378]	training's binary_logloss: 0.000899409	valid_1's binary_logloss: 0.00143401
[379]	training's binary_logloss: 0.000896259	valid_1's binary_logloss: 0.00143285
[380]	training's binary_logloss: 0.00089282	valid_1's binary_logloss: 0.00143152
[381]	training's binary_logloss: 0.000890063	valid_1's binary_logloss: 0.00143016
[382]	training's binary_logloss: 0.000887	valid_1's binary_logloss: 0.00142962
[383]	training's binary_logloss: 0.000884214	valid_1's binary_logloss: 0.00142863
[384]	training's binary_logloss: 0.000881531	valid_1's binary_logloss: 0.00142739
[385]	training's binary_logloss: 0.000878879	valid_1's binary_logloss: 0.00142559
[386]	training's binary_logloss: 0.000875924	valid_1's binary_logloss: 0.00142455
[387]	training's binary_logloss: 0.000873582	valid_1's binary_logloss: 0.00142361
[388]	training's binary_logloss: 0.000870534	valid_1's binary_logloss: 0.00142248
[389]	training's bin

[479]	training's binary_logloss: 0.000683728	valid_1's binary_logloss: 0.00137034
[480]	training's binary_logloss: 0.000682033	valid_1's binary_logloss: 0.00137018
[481]	training's binary_logloss: 0.000680296	valid_1's binary_logloss: 0.00136983
[482]	training's binary_logloss: 0.000678901	valid_1's binary_logloss: 0.00136978
[483]	training's binary_logloss: 0.000677225	valid_1's binary_logloss: 0.00137019
[484]	training's binary_logloss: 0.000675547	valid_1's binary_logloss: 0.00137017
[485]	training's binary_logloss: 0.00067404	valid_1's binary_logloss: 0.00137013
[486]	training's binary_logloss: 0.000672588	valid_1's binary_logloss: 0.00136957
[487]	training's binary_logloss: 0.000671291	valid_1's binary_logloss: 0.0013689
[488]	training's binary_logloss: 0.000669649	valid_1's binary_logloss: 0.00136856
[489]	training's binary_logloss: 0.000668027	valid_1's binary_logloss: 0.00136695
[490]	training's binary_logloss: 0.000666734	valid_1's binary_logloss: 0.0013665
[491]	training's bi

KeyboardInterrupt: 

In [38]:
clazzs = ['empty', 'wildebeest', 'zebra', 'gazellethomsons', 'buffalo',
'elephant', 'hartebeest', 'impala', 'gazellegrants', 'giraffe',
'warthog', 'guineafowl', 'otherbird']


        
for clazz in clazzs:
    
#     feature_classes=feature_classes_d.get(clazz, list(train_labels_columns))
    feature_classes=default_classes

    columns = ['pred_model_480_360_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img3_' + c for c in feature_classes] +\
    ['mean_backs_' + c for c in feature_classes] +\
    ['median_img1_' + c for c in feature_classes] +\
    ['median_img2_' + c for c in feature_classes] +\
    ['median_img3_' + c for c in feature_classes] +\
    ['mean_combines_' + c for c in feature_classes] +\
    ['c_' + str(i) for i in good_classes] +\
    ['c2_' + str(i) for i in good_classes] +\
    ['c3_' + str(i) for i in good_classes]+\
    ['hour', 'month']



    X_train = train_dataset[columns]
    y_train = train_dataset[clazz]
    X_val = val_dataset[columns]
    y_val = val_dataset[clazz]

    lgb_train = lgb.Dataset(X_train, y_train)
    lgb_val = lgb.Dataset(X_val, y_val, reference=lgb_train)

    params = {
                'boosting_type': 'gbdt',
                'objective': 'binary',
                'metric': {'binary_logloss'},
                'num_leaves': num_leaves.get(clazz, 32),
                'max_depth': max_depth.get(clazz, 6),
                'learning_rate': learning_rate.get(clazz, 0.009),
                'feature_fraction':  feature_fraction.get(clazz, 0.6),
                'bagging_fraction': bagging_fraction.get(clazz, 0.8),
                'bagging_freq': bagging_freq.get(clazz, 5),
                'scale_pos_weight':scale_pos_weight.get(clazz, 1),
                'lambda_l1':lambda_l1.get(clazz, 0.2),
                'lambda_l2':lambda_l2.get(clazz, 0.2),
                'min_child_samples':min_child_samples.get(clazz, 25),

    }

    gbm = lgb.train(params,
                        lgb_train,
                        num_boost_round=3000,
                        valid_sets=[lgb_train, lgb_val],
                        early_stopping_rounds=20)
    gbm.save_model("lgbs_v7/" + clazz + '.txt', num_iteration=gbm.best_iteration) 

    X_test = test_dataset[columns]
    y_test = test_dataset[clazz]
    
    print(clazz, log_loss(y_test, gbm.predict(X_test.values)))
    gc.collect()
    

[1]	training's binary_logloss: 0.511115	valid_1's binary_logloss: 0.491504
Training until validation scores don't improve for 20 rounds
[2]	training's binary_logloss: 0.502959	valid_1's binary_logloss: 0.483751
[3]	training's binary_logloss: 0.495355	valid_1's binary_logloss: 0.47655
[4]	training's binary_logloss: 0.487747	valid_1's binary_logloss: 0.46936
[5]	training's binary_logloss: 0.48037	valid_1's binary_logloss: 0.462318
[6]	training's binary_logloss: 0.473157	valid_1's binary_logloss: 0.45545
[7]	training's binary_logloss: 0.466145	valid_1's binary_logloss: 0.44878
[8]	training's binary_logloss: 0.459368	valid_1's binary_logloss: 0.442308
[9]	training's binary_logloss: 0.452817	valid_1's binary_logloss: 0.436056
[10]	training's binary_logloss: 0.446439	valid_1's binary_logloss: 0.429968
[11]	training's binary_logloss: 0.440496	valid_1's binary_logloss: 0.424364
[12]	training's binary_logloss: 0.434384	valid_1's binary_logloss: 0.418544
[13]	training's binary_logloss: 0.428451	

[110]	training's binary_logloss: 0.158177	valid_1's binary_logloss: 0.153757
[111]	training's binary_logloss: 0.156841	valid_1's binary_logloss: 0.152479
[112]	training's binary_logloss: 0.155522	valid_1's binary_logloss: 0.151214
[113]	training's binary_logloss: 0.154223	valid_1's binary_logloss: 0.149964
[114]	training's binary_logloss: 0.152979	valid_1's binary_logloss: 0.148772
[115]	training's binary_logloss: 0.151716	valid_1's binary_logloss: 0.147558
[116]	training's binary_logloss: 0.150459	valid_1's binary_logloss: 0.146348
[117]	training's binary_logloss: 0.149224	valid_1's binary_logloss: 0.145158
[118]	training's binary_logloss: 0.147996	valid_1's binary_logloss: 0.143982
[119]	training's binary_logloss: 0.146787	valid_1's binary_logloss: 0.142815
[120]	training's binary_logloss: 0.145596	valid_1's binary_logloss: 0.141658
[121]	training's binary_logloss: 0.144415	valid_1's binary_logloss: 0.140518
[122]	training's binary_logloss: 0.143235	valid_1's binary_logloss: 0.139384

[216]	training's binary_logloss: 0.0738969	valid_1's binary_logloss: 0.0729985
[217]	training's binary_logloss: 0.0734616	valid_1's binary_logloss: 0.0725838
[218]	training's binary_logloss: 0.0730239	valid_1's binary_logloss: 0.0721702
[219]	training's binary_logloss: 0.0725961	valid_1's binary_logloss: 0.0717687
[220]	training's binary_logloss: 0.072165	valid_1's binary_logloss: 0.0713609
[221]	training's binary_logloss: 0.0717381	valid_1's binary_logloss: 0.0709529
[222]	training's binary_logloss: 0.0713209	valid_1's binary_logloss: 0.0705558
[223]	training's binary_logloss: 0.0709073	valid_1's binary_logloss: 0.0701682
[224]	training's binary_logloss: 0.0704935	valid_1's binary_logloss: 0.0697726
[225]	training's binary_logloss: 0.0700885	valid_1's binary_logloss: 0.0693895
[226]	training's binary_logloss: 0.0696901	valid_1's binary_logloss: 0.0690177
[227]	training's binary_logloss: 0.0692942	valid_1's binary_logloss: 0.0686429
[228]	training's binary_logloss: 0.0688942	valid_1's 

[321]	training's binary_logloss: 0.0445023	valid_1's binary_logloss: 0.0454442
[322]	training's binary_logloss: 0.044335	valid_1's binary_logloss: 0.0452932
[323]	training's binary_logloss: 0.0441693	valid_1's binary_logloss: 0.0451456
[324]	training's binary_logloss: 0.0440078	valid_1's binary_logloss: 0.0450048
[325]	training's binary_logloss: 0.0438461	valid_1's binary_logloss: 0.0448566
[326]	training's binary_logloss: 0.0436876	valid_1's binary_logloss: 0.0447105
[327]	training's binary_logloss: 0.0435317	valid_1's binary_logloss: 0.0445684
[328]	training's binary_logloss: 0.0433741	valid_1's binary_logloss: 0.0444248
[329]	training's binary_logloss: 0.043218	valid_1's binary_logloss: 0.0442906
[330]	training's binary_logloss: 0.0430652	valid_1's binary_logloss: 0.0441531
[331]	training's binary_logloss: 0.0429111	valid_1's binary_logloss: 0.0440145
[332]	training's binary_logloss: 0.0427591	valid_1's binary_logloss: 0.0438756
[333]	training's binary_logloss: 0.0426099	valid_1's b

[426]	training's binary_logloss: 0.0331041	valid_1's binary_logloss: 0.0354385
[427]	training's binary_logloss: 0.0330405	valid_1's binary_logloss: 0.0353841
[428]	training's binary_logloss: 0.0329721	valid_1's binary_logloss: 0.0353286
[429]	training's binary_logloss: 0.0329058	valid_1's binary_logloss: 0.0352738
[430]	training's binary_logloss: 0.032841	valid_1's binary_logloss: 0.0352205
[431]	training's binary_logloss: 0.0327752	valid_1's binary_logloss: 0.0351691
[432]	training's binary_logloss: 0.0327101	valid_1's binary_logloss: 0.035117
[433]	training's binary_logloss: 0.0326463	valid_1's binary_logloss: 0.0350657
[434]	training's binary_logloss: 0.0325834	valid_1's binary_logloss: 0.0350184
[435]	training's binary_logloss: 0.0325187	valid_1's binary_logloss: 0.0349653
[436]	training's binary_logloss: 0.0324553	valid_1's binary_logloss: 0.0349131
[437]	training's binary_logloss: 0.0323946	valid_1's binary_logloss: 0.0348577
[438]	training's binary_logloss: 0.0323325	valid_1's b

...

[341]	training's binary_logloss: 0.000294874	valid_1's binary_logloss: 0.00280808
[342]	training's binary_logloss: 0.000292922	valid_1's binary_logloss: 0.00280592
[343]	training's binary_logloss: 0.000291055	valid_1's binary_logloss: 0.00280442
[344]	training's binary_logloss: 0.000289164	valid_1's binary_logloss: 0.00280294
[345]	training's binary_logloss: 0.000287361	valid_1's binary_logloss: 0.00280156
[346]	training's binary_logloss: 0.000285525	valid_1's binary_logloss: 0.00279919
[347]	training's binary_logloss: 0.000283626	valid_1's binary_logloss: 0.0027976
[348]	training's binary_logloss: 0.000281732	valid_1's binary_logloss: 0.00279581
[349]	training's binary_logloss: 0.000279955	valid_1's binary_logloss: 0.00279394
[350]	training's binary_logloss: 0.000278157	valid_1's binary_logloss: 0.00279285
[351]	training's binary_logloss: 0.000276449	valid_1's binary_logloss: 0.00279232
[352]	training's binary_logloss: 0.000274709	valid_1's binary_logloss: 0.00279121
[353]	training's 

[11]	training's binary_logloss: 0.01483	valid_1's binary_logloss: 0.0174764
[12]	training's binary_logloss: 0.0145922	valid_1's binary_logloss: 0.0172599
[13]	training's binary_logloss: 0.0143592	valid_1's binary_logloss: 0.0170661
[14]	training's binary_logloss: 0.0141444	valid_1's binary_logloss: 0.0168869
[15]	training's binary_logloss: 0.0139466	valid_1's binary_logloss: 0.016723
[16]	training's binary_logloss: 0.0137537	valid_1's binary_logloss: 0.0165552
[17]	training's binary_logloss: 0.0135677	valid_1's binary_logloss: 0.0163896
[18]	training's binary_logloss: 0.0133961	valid_1's binary_logloss: 0.0162527
[19]	training's binary_logloss: 0.0132337	valid_1's binary_logloss: 0.016122
[20]	training's binary_logloss: 0.0130761	valid_1's binary_logloss: 0.0159899
[21]	training's binary_logloss: 0.012924	valid_1's binary_logloss: 0.015878
[22]	training's binary_logloss: 0.0127791	valid_1's binary_logloss: 0.0157564
[23]	training's binary_logloss: 0.0126449	valid_1's binary_logloss: 0.

[116]	training's binary_logloss: 0.00744851	valid_1's binary_logloss: 0.0119511
[117]	training's binary_logloss: 0.00742289	valid_1's binary_logloss: 0.0119402
[118]	training's binary_logloss: 0.00739752	valid_1's binary_logloss: 0.011928
[119]	training's binary_logloss: 0.00737331	valid_1's binary_logloss: 0.0119195
[120]	training's binary_logloss: 0.00734893	valid_1's binary_logloss: 0.0119091
[121]	training's binary_logloss: 0.00732335	valid_1's binary_logloss: 0.0118958
[122]	training's binary_logloss: 0.00729905	valid_1's binary_logloss: 0.0118809
[123]	training's binary_logloss: 0.00727337	valid_1's binary_logloss: 0.0118693
[124]	training's binary_logloss: 0.00724915	valid_1's binary_logloss: 0.0118574
[125]	training's binary_logloss: 0.00722341	valid_1's binary_logloss: 0.0118461
[126]	training's binary_logloss: 0.00719981	valid_1's binary_logloss: 0.0118318
[127]	training's binary_logloss: 0.00717687	valid_1's binary_logloss: 0.0118219
[128]	training's binary_logloss: 0.007154

[219]	training's binary_logloss: 0.00574947	valid_1's binary_logloss: 0.0111833
[220]	training's binary_logloss: 0.00573927	valid_1's binary_logloss: 0.0111803
[221]	training's binary_logloss: 0.00572809	valid_1's binary_logloss: 0.0111774
[222]	training's binary_logloss: 0.00571802	valid_1's binary_logloss: 0.0111752
[223]	training's binary_logloss: 0.00570762	valid_1's binary_logloss: 0.0111728
[224]	training's binary_logloss: 0.00569625	valid_1's binary_logloss: 0.0111679
[225]	training's binary_logloss: 0.00568574	valid_1's binary_logloss: 0.0111656
[226]	training's binary_logloss: 0.00567622	valid_1's binary_logloss: 0.0111615
[227]	training's binary_logloss: 0.00566615	valid_1's binary_logloss: 0.0111595
[228]	training's binary_logloss: 0.00565473	valid_1's binary_logloss: 0.0111553
[229]	training's binary_logloss: 0.00564548	valid_1's binary_logloss: 0.0111524
[230]	training's binary_logloss: 0.00563676	valid_1's binary_logloss: 0.0111489
[231]	training's binary_logloss: 0.00562

[323]	training's binary_logloss: 0.00489987	valid_1's binary_logloss: 0.0110001
[324]	training's binary_logloss: 0.00489169	valid_1's binary_logloss: 0.0109953
[325]	training's binary_logloss: 0.00488402	valid_1's binary_logloss: 0.0109949
[326]	training's binary_logloss: 0.00487622	valid_1's binary_logloss: 0.010995
[327]	training's binary_logloss: 0.00487014	valid_1's binary_logloss: 0.0109941
[328]	training's binary_logloss: 0.00486361	valid_1's binary_logloss: 0.0109934
[329]	training's binary_logloss: 0.00485699	valid_1's binary_logloss: 0.0109907
[330]	training's binary_logloss: 0.00485127	valid_1's binary_logloss: 0.0109887
[331]	training's binary_logloss: 0.00484296	valid_1's binary_logloss: 0.0109879
[332]	training's binary_logloss: 0.00483681	valid_1's binary_logloss: 0.0109873
[333]	training's binary_logloss: 0.00483115	valid_1's binary_logloss: 0.0109856
[334]	training's binary_logloss: 0.00482594	valid_1's binary_logloss: 0.0109859
[335]	training's binary_logloss: 0.004820

In [39]:
clazzs = ['empty', 'wildebeest', 'zebra', 'gazellethomsons', 'buffalo',
'elephant', 'hartebeest', 'impala', 'gazellegrants', 'giraffe',
'warthog', 'guineafowl', 'otherbird']


        
for clazz in clazzs:
    
#     feature_classes=feature_classes_d.get(clazz, list(train_labels_columns))
    feature_classes=default_classes

    columns = ['pred_model_480_360_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img3_' + c for c in feature_classes] +\
    ['mean_backs_' + c for c in feature_classes] +\
    ['median_img1_' + c for c in feature_classes] +\
    ['median_img2_' + c for c in feature_classes] +\
    ['median_img3_' + c for c in feature_classes] +\
    ['mean_combines_' + c for c in feature_classes] +\
    ['hour', 'month']



    X_train = train_dataset[columns]
    y_train = train_dataset[clazz]
    X_val = val_dataset[columns]
    y_val = val_dataset[clazz]

    lgb_train = lgb.Dataset(X_train, y_train)
    lgb_val = lgb.Dataset(X_val, y_val, reference=lgb_train)

    params = {
                'boosting_type': 'gbdt',
                'objective': 'binary',
                'metric': {'binary_logloss'},
                'num_leaves': num_leaves.get(clazz, 32),
                'max_depth': max_depth.get(clazz, 6),
                'learning_rate': learning_rate.get(clazz, 0.009),
                'feature_fraction':  feature_fraction.get(clazz, 0.6),
                'bagging_fraction': bagging_fraction.get(clazz, 0.8),
                'bagging_freq': bagging_freq.get(clazz, 5),
                'scale_pos_weight':scale_pos_weight.get(clazz, 1),
                'lambda_l1':lambda_l1.get(clazz, 0.2),
                'lambda_l2':lambda_l2.get(clazz, 0.2),
                'min_child_samples':min_child_samples.get(clazz, 25),

    }

    gbm = lgb.train(params,
                        lgb_train,
                        num_boost_round=3000,
                        valid_sets=[lgb_train, lgb_val],
                        early_stopping_rounds=20)
    gbm.save_model("lgbs_v7/" + clazz + '.txt', num_iteration=gbm.best_iteration) 

    X_test = test_dataset[columns]
    y_test = test_dataset[clazz]
    
    print(clazz, log_loss(y_test, gbm.predict(X_test.values)))
    gc.collect()
    

[1]	training's binary_logloss: 0.511116	valid_1's binary_logloss: 0.491505
Training until validation scores don't improve for 20 rounds
[2]	training's binary_logloss: 0.502915	valid_1's binary_logloss: 0.483714
[3]	training's binary_logloss: 0.494991	valid_1's binary_logloss: 0.47618
[4]	training's binary_logloss: 0.48732	valid_1's binary_logloss: 0.46888
[5]	training's binary_logloss: 0.479918	valid_1's binary_logloss: 0.461821
[6]	training's binary_logloss: 0.472711	valid_1's binary_logloss: 0.454957
[7]	training's binary_logloss: 0.465747	valid_1's binary_logloss: 0.448306
[8]	training's binary_logloss: 0.458991	valid_1's binary_logloss: 0.441864
[9]	training's binary_logloss: 0.452453	valid_1's binary_logloss: 0.435613
[10]	training's binary_logloss: 0.44603	valid_1's binary_logloss: 0.429504
[11]	training's binary_logloss: 0.439844	valid_1's binary_logloss: 0.42358
[12]	training's binary_logloss: 0.433782	valid_1's binary_logloss: 0.417802
[13]	training's binary_logloss: 0.427875	

[109]	training's binary_logloss: 0.159502	valid_1's binary_logloss: 0.154904
[110]	training's binary_logloss: 0.158154	valid_1's binary_logloss: 0.153608
[111]	training's binary_logloss: 0.156821	valid_1's binary_logloss: 0.152329
[112]	training's binary_logloss: 0.155502	valid_1's binary_logloss: 0.151062
[113]	training's binary_logloss: 0.154214	valid_1's binary_logloss: 0.149824
[114]	training's binary_logloss: 0.152979	valid_1's binary_logloss: 0.148636
[115]	training's binary_logloss: 0.151706	valid_1's binary_logloss: 0.147411
[116]	training's binary_logloss: 0.150455	valid_1's binary_logloss: 0.146209
[117]	training's binary_logloss: 0.149213	valid_1's binary_logloss: 0.145013
[118]	training's binary_logloss: 0.147984	valid_1's binary_logloss: 0.143831
[119]	training's binary_logloss: 0.146768	valid_1's binary_logloss: 0.142664
[120]	training's binary_logloss: 0.145565	valid_1's binary_logloss: 0.14151
[121]	training's binary_logloss: 0.144376	valid_1's binary_logloss: 0.140363


[216]	training's binary_logloss: 0.0739548	valid_1's binary_logloss: 0.0728552
[217]	training's binary_logloss: 0.0735188	valid_1's binary_logloss: 0.0724398
[218]	training's binary_logloss: 0.0730867	valid_1's binary_logloss: 0.0720267
[219]	training's binary_logloss: 0.0726581	valid_1's binary_logloss: 0.0716179
[220]	training's binary_logloss: 0.072228	valid_1's binary_logloss: 0.0712079
[221]	training's binary_logloss: 0.0718145	valid_1's binary_logloss: 0.0708208
[222]	training's binary_logloss: 0.0713972	valid_1's binary_logloss: 0.070429
[223]	training's binary_logloss: 0.0709798	valid_1's binary_logloss: 0.0700311
[224]	training's binary_logloss: 0.0705756	valid_1's binary_logloss: 0.0696516
[225]	training's binary_logloss: 0.0701654	valid_1's binary_logloss: 0.0692654
[226]	training's binary_logloss: 0.0697594	valid_1's binary_logloss: 0.0688802
[227]	training's binary_logloss: 0.0693551	valid_1's binary_logloss: 0.068497
[228]	training's binary_logloss: 0.0689631	valid_1's bi

[321]	training's binary_logloss: 0.0446267	valid_1's binary_logloss: 0.0452867
[322]	training's binary_logloss: 0.0444717	valid_1's binary_logloss: 0.0451446
[323]	training's binary_logloss: 0.0443087	valid_1's binary_logloss: 0.0449999
[324]	training's binary_logloss: 0.0441441	valid_1's binary_logloss: 0.0448512
[325]	training's binary_logloss: 0.0439823	valid_1's binary_logloss: 0.044703
[326]	training's binary_logloss: 0.0438212	valid_1's binary_logloss: 0.0445565
[327]	training's binary_logloss: 0.0436606	valid_1's binary_logloss: 0.0444117
[328]	training's binary_logloss: 0.0435032	valid_1's binary_logloss: 0.0442692
[329]	training's binary_logloss: 0.0433473	valid_1's binary_logloss: 0.044126
[330]	training's binary_logloss: 0.0431917	valid_1's binary_logloss: 0.0439862
[331]	training's binary_logloss: 0.0430385	valid_1's binary_logloss: 0.0438453
[332]	training's binary_logloss: 0.0428918	valid_1's binary_logloss: 0.0437106
[333]	training's binary_logloss: 0.0427398	valid_1's b

[425]	training's binary_logloss: 0.0333055	valid_1's binary_logloss: 0.035285
[426]	training's binary_logloss: 0.0332374	valid_1's binary_logloss: 0.0352248
[427]	training's binary_logloss: 0.0331695	valid_1's binary_logloss: 0.0351716
[428]	training's binary_logloss: 0.0331053	valid_1's binary_logloss: 0.0351184
[429]	training's binary_logloss: 0.0330394	valid_1's binary_logloss: 0.0350652
[430]	training's binary_logloss: 0.0329733	valid_1's binary_logloss: 0.0350141
[431]	training's binary_logloss: 0.0329083	valid_1's binary_logloss: 0.0349594
[432]	training's binary_logloss: 0.0328438	valid_1's binary_logloss: 0.0349067
[433]	training's binary_logloss: 0.0327796	valid_1's binary_logloss: 0.0348553
[434]	training's binary_logloss: 0.0327176	valid_1's binary_logloss: 0.0348044
[435]	training's binary_logloss: 0.0326565	valid_1's binary_logloss: 0.0347564
[436]	training's binary_logloss: 0.032594	valid_1's binary_logloss: 0.0347056
[437]	training's binary_logloss: 0.0325352	valid_1's b

...

[300]	training's binary_logloss: 0.000392625	valid_1's binary_logloss: 0.00286186
[301]	training's binary_logloss: 0.000389719	valid_1's binary_logloss: 0.0028597
[302]	training's binary_logloss: 0.000387017	valid_1's binary_logloss: 0.00285682
[303]	training's binary_logloss: 0.000384474	valid_1's binary_logloss: 0.00285348
[304]	training's binary_logloss: 0.000381865	valid_1's binary_logloss: 0.00285201
[305]	training's binary_logloss: 0.000379246	valid_1's binary_logloss: 0.0028487
[306]	training's binary_logloss: 0.000376606	valid_1's binary_logloss: 0.00284517
[307]	training's binary_logloss: 0.000373922	valid_1's binary_logloss: 0.00284263
[308]	training's binary_logloss: 0.00037132	valid_1's binary_logloss: 0.00284079
[309]	training's binary_logloss: 0.000368787	valid_1's binary_logloss: 0.00283863
[310]	training's binary_logloss: 0.000366314	valid_1's binary_logloss: 0.00283586
[311]	training's binary_logloss: 0.000363841	valid_1's binary_logloss: 0.0028342
[312]	training's bin

[402]	training's binary_logloss: 0.000204462	valid_1's binary_logloss: 0.00271393
[403]	training's binary_logloss: 0.000203181	valid_1's binary_logloss: 0.00271463
[404]	training's binary_logloss: 0.000202018	valid_1's binary_logloss: 0.00271516
[405]	training's binary_logloss: 0.000200847	valid_1's binary_logloss: 0.0027151
[406]	training's binary_logloss: 0.000199684	valid_1's binary_logloss: 0.00271534
[407]	training's binary_logloss: 0.000198549	valid_1's binary_logloss: 0.00271584
[408]	training's binary_logloss: 0.000197394	valid_1's binary_logloss: 0.00271589
[409]	training's binary_logloss: 0.000196217	valid_1's binary_logloss: 0.00271647
[410]	training's binary_logloss: 0.000195076	valid_1's binary_logloss: 0.00271722
[411]	training's binary_logloss: 0.000193837	valid_1's binary_logloss: 0.00271671
[412]	training's binary_logloss: 0.000192624	valid_1's binary_logloss: 0.00271604
[413]	training's binary_logloss: 0.00019157	valid_1's binary_logloss: 0.00271468
[414]	training's b

[65]	training's binary_logloss: 0.00938327	valid_1's binary_logloss: 0.0127577
[66]	training's binary_logloss: 0.0093325	valid_1's binary_logloss: 0.0127273
[67]	training's binary_logloss: 0.0092841	valid_1's binary_logloss: 0.0126954
[68]	training's binary_logloss: 0.00923636	valid_1's binary_logloss: 0.0126654
[69]	training's binary_logloss: 0.00918899	valid_1's binary_logloss: 0.0126355
[70]	training's binary_logloss: 0.00914294	valid_1's binary_logloss: 0.0126057
[71]	training's binary_logloss: 0.00909716	valid_1's binary_logloss: 0.0125754
[72]	training's binary_logloss: 0.00905301	valid_1's binary_logloss: 0.0125461
[73]	training's binary_logloss: 0.00900922	valid_1's binary_logloss: 0.0125187
[74]	training's binary_logloss: 0.00896547	valid_1's binary_logloss: 0.0124931
[75]	training's binary_logloss: 0.00892218	valid_1's binary_logloss: 0.0124673
[76]	training's binary_logloss: 0.00887795	valid_1's binary_logloss: 0.0124399
[77]	training's binary_logloss: 0.00883817	valid_1's b

[170]	training's binary_logloss: 0.00653428	valid_1's binary_logloss: 0.0112938
[171]	training's binary_logloss: 0.0065195	valid_1's binary_logloss: 0.0112881
[172]	training's binary_logloss: 0.00650487	valid_1's binary_logloss: 0.0112836
[173]	training's binary_logloss: 0.00649052	valid_1's binary_logloss: 0.0112796
[174]	training's binary_logloss: 0.00647674	valid_1's binary_logloss: 0.011273
[175]	training's binary_logloss: 0.00646197	valid_1's binary_logloss: 0.0112667
[176]	training's binary_logloss: 0.00644852	valid_1's binary_logloss: 0.0112612
[177]	training's binary_logloss: 0.00643494	valid_1's binary_logloss: 0.0112574
[178]	training's binary_logloss: 0.00642101	valid_1's binary_logloss: 0.0112525
[179]	training's binary_logloss: 0.00640663	valid_1's binary_logloss: 0.0112446
[180]	training's binary_logloss: 0.00639159	valid_1's binary_logloss: 0.0112411
[181]	training's binary_logloss: 0.00637725	valid_1's binary_logloss: 0.0112343
[182]	training's binary_logloss: 0.0063635

[273]	training's binary_logloss: 0.00542505	valid_1's binary_logloss: 0.0110047
[274]	training's binary_logloss: 0.00541776	valid_1's binary_logloss: 0.011005
[275]	training's binary_logloss: 0.0054114	valid_1's binary_logloss: 0.0110035
[276]	training's binary_logloss: 0.00540293	valid_1's binary_logloss: 0.0110037
[277]	training's binary_logloss: 0.00539384	valid_1's binary_logloss: 0.011005
[278]	training's binary_logloss: 0.00538392	valid_1's binary_logloss: 0.0110052
[279]	training's binary_logloss: 0.00537548	valid_1's binary_logloss: 0.0110057
[280]	training's binary_logloss: 0.00536666	valid_1's binary_logloss: 0.0110067
[281]	training's binary_logloss: 0.00535888	valid_1's binary_logloss: 0.0110043
[282]	training's binary_logloss: 0.00535105	valid_1's binary_logloss: 0.0110045
[283]	training's binary_logloss: 0.00534367	valid_1's binary_logloss: 0.0110042
[284]	training's binary_logloss: 0.0053358	valid_1's binary_logloss: 0.0110042
[285]	training's binary_logloss: 0.00532796	

In [27]:
gc.collect()

138

In [17]:
    feature_classes=default_classes

    columns = ['pred_model_480_360_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as480_img3_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_480_360_v2_as512_img3_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img1_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img2_' + c for c in feature_classes] +\
    ['pred_model_512_384_v2_as512_img3_' + c for c in feature_classes] +\
    ['mean_backs_' + c for c in feature_classes] +\
    ['median_img1_' + c for c in feature_classes] +\
    ['median_img2_' + c for c in feature_classes] +\
    ['median_img3_' + c for c in feature_classes] +\
    ['mean_combines_' + c for c in feature_classes] +\
    ['hour', 'month']

In [22]:
line=train_dataset[columns].loc['SER_S9#B03#1#1'].values

In [57]:
line[810:840]

array([0.00000000e+00, 4.47035000e-08, 0.00000000e+00, 1.63913000e-07,
       8.79168500e-07, 5.96045000e-08, 4.84287700e-06, 0.00000000e+00,
       1.05798245e-05, 3.08156010e-05, 7.00000000e+00, 6.00000000e+00])